Vague words

1. Load vague words set
> Based on the QUARS++ work https://github.com/ISTI-FMT/QUARS_plus_plus

In [ ]:
import requests
vaguewords = requests.get('https://raw.githubusercontent.com/ISTI-FMT/QUARS_plus_plus/master/jape_rules/vagueness/vague.lst')
vagues = []

for vword in vaguewords.text.splitlines():
  vagues = vagues + [vword.lower()]

vagues.pop()
vagues = list(dict.fromkeys(vagues))
print (vagues)

2. Load user stories
> With another dataset: 
 * Load different Excel file
 * Consider whether there is a language column

In [2]:
import pandas as pd
import openpyxl

res = pd.read_excel("vsys.xlsx", sheet_name="code")
res.head()

dutch = res

3. Translate Dutch to English - run once, then save to file

In [ ]:
from googletrans import Translator
translator = Translator()
 
english2 = []
for us in res['Idea'].values.tolist():
  translated = translator.translate(us, dest = 'en').text
  english2.append(translated)

print (english2)

dict = {'dutch': dutch['Idea'].values.tolist(), 'english': english2}  
       
df2 = pd.DataFrame(dict) 
    
# saving the dataframe 
df2.to_csv('translation.csv', index=False) 

In [ ]:
col_list = ["english"]
df2 = pd.read_csv('translation.csv', usecols=col_list)


english2 = []
for index, stmt in df2.iterrows():
    english2.append(stmt["english"])

print(english2)


4. Find vague words
> Saves them to vague_hits.csv

In [ ]:
import re

def string_found(string1, string2):
   if re.search(r"\b" + re.escape(string1) + r"\b", string2):
      return True
   return False


vague_hits = []

n = 1
for us in [*english2]:
  identified = False
  for word in vagues:
    if string_found(word, us.lower()):
      identified = True
      print (str(n) + " - " + word + " --- " + us)
      vague_hits.append([word, us])
  if (identified):
    n = n + 1

import csv
  
fields = ['Vague Word', 'Req'] 
    
with open('vague_hits.csv', 'w') as f:
      
    write = csv.writer(f, delimiter = ";")
    write.writerow(fields)
    write.writerows(vague_hits)

5. Readability metrics

In [6]:
import textstat
flesch = []
ari = []
combined = [*english2]
for us in combined:
  flesch.append(textstat.flesch_reading_ease(us))
  ari.append(textstat.automated_readability_index(us))

dict = {'us' : [*english2], 'flesch': flesch, 'ari': ari}  
       
df3 = pd.DataFrame(dict) 
df3.head()
df3.to_csv('readability.csv', index=False, sep = ";") 